In [26]:
import pandas as pd
import os
import time
import csv
import re
import codecs
import requests
from bs4 import BeautifulSoup
 
import datetime
    
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.keys import Keys
from selenium.common.exceptions import NoSuchElementException, \
        TimeoutException, ElementNotInteractableException, ElementClickInterceptedException

In [2]:
def text_file_to_dataframe(filename):
    # Check if the text file exists
    if os.path.exists(filename):
        
        # Read the text file and create a list of lines
        with open(filename, "r") as file:
            lines = file.readlines()
            content = [line.strip() for line in lines]

        # Create a DataFrame from the list
        df = pd.DataFrame(content, columns=['links'])
        
        return df
    else:
        print(f"{filename} does not exist.")
        return None

# Loading Links & Creating DataFrame

In [32]:
input_filename = 'final_links_again.txt'
df = text_file_to_dataframe(input_filename)

In [33]:
# new cell

df = df[730:1361]

In [34]:
# reset index to start at zero

df.reset_index(drop = True, inplace = True)
df.shape

(631, 1)

# Scraper Code

In [6]:
# # S C R A P I N G   B R O W S E R
# driver = webdriver.Firefox()

In [7]:
# df['links'].iloc[4]

In [8]:
# driver.get('https://www.goodreads.com/choiceawards/best-fantasy-books-2022')

In [9]:
# button = driver.find_element_by_css_selector('button[aria-label="Book details and editions"]')

In [10]:
# button.click()

In [11]:
# close_button = driver.find_element_by_class_name('gr-iconButton')
# close_button.text

In [12]:
# close_button = driver.find_element_by_css_selector('.gr-iconButton')
# close_button.click()


In [13]:
# <span class="Button__labelItem">Book details &amp; editions</span>

In [7]:
import selenium

In [8]:
selenium.__version__


'4.8.2'

In [38]:
# Define a function to extract the publisher element text
def get_publisher_text():
    try:
        # Find the element with the EditionDetails class
        time.sleep(10)
        edition_details_element = WebDriverWait(driver, edition_details_element_WebDriverWait_amount).until(EC.presence_of_element_located((By.CLASS_NAME, 'EditionDetails')))
        
        # Find the nested element with the data-testid attribute
        publisher_element = edition_details_element.find_element(By.CSS_SELECTOR, 'div[data-testid="contentContainer"]')

        
        return publisher_element[1].text

    except NoSuchElementException:
        return ""
    except TimeoutException:
        print("Timeout: EditionDetails element not found within the specified time")
        return ""
    except ElementClickInterceptedException:
        return ""

### This is the updated, v12

In [ ]:
# S C R A P I N G   B R O W S E R
driver = webdriver.Chrome()

reviews_file_exists = os.path.isfile("reviews.csv")
index_file_exists = os.path.isfile("index.txt")

# checking last value of index in order to continue from last position
if index_file_exists:
    with open("index.txt", "r") as index_file:
        last_index = int(index_file.read())
else:
    last_index = 0

print(f"Output of last_index: {last_index}")
#============================================================================================================
# T I M E   W A I T   S E T T I N G S
#============================================================================================================
synopsis_and_review_wait_amount = 7
publisher_click_wait_amount = 7

title_element_WebDriverWait_amount = 5
synopsis_and_review_list_WebDriverWait_amount = 30
edition_details_element_WebDriverWait_amount = 5


# iterate over the dataframe
for index, row in df.iloc[last_index:].iterrows():
    #============================================================================================================
    # L O A D    P A G E    O N    S C R A P I N G    B R O W S E R
    #============================================================================================================
    driver.get(row['links'])
    
    #============================================================================================================
    # M E A T   A N D   P O T A T O E S
    #============================================================================================================
    try:
        print(f"- Waiting {synopsis_and_review_wait_amount} Seconds for Synopsis and Reviews to load....")
        time.sleep(synopsis_and_review_wait_amount)
        synopsis_and_review_list = WebDriverWait(driver, 
                synopsis_and_review_list_WebDriverWait_amount).until(EC.presence_of_all_elements_located(
                (By.CLASS_NAME, 'Formatted')))
        synopsis_length = len(synopsis_and_review_list)
    except TimeoutException:
        print(f"Timed out while waiting for synopsis and review list for book {title}, moving on to next book")
        continue
    #============================================================================================================
    # T I T L E
    #============================================================================================================
    try:
        title_element = WebDriverWait(driver, title_element_WebDriverWait_amount).until(EC.presence_of_element_located((By.CLASS_NAME, 'BookPageTitleSection__title')))
        title = title_element.text
    except TimeoutException:
        print(f"Timed out while waiting for title for book {row['links']}, moving on to next book")
        continue

    #============================================================================================================
    # P U B L I S H E R
    #============================================================================================================
    # First, try to find and click the button
    try:
        button = driver.find_element(By.CSS_SELECTOR, '//button[aria-label="Book details and editions"]')
        button.click()
        
        # if no exception from click() then assign "Pass"
        clicked_button_test = "Pass"
        
        # waiting for elements to load after clicking button
        time.sleep(publisher_click_wait_amount)
        print(f"- Waiting {publisher_click_wait_amount} seconds after clicking button")
        # run the get_publisher_text function for 1st time
        publisher = get_publisher_text(edition_details_element_WebDriverWait_amount)
        
    except (NoSuchElementException):
        print("Button not found")
        try:
            publisher = get_publisher_text(edition_details_element_WebDriverWait_amount)
            clicked_button_test = "Pass"
        except:
            publisher=""
            clicked_button_test = "Fail"
    except (ElementNotInteractableException, ElementClickInterceptedException):
        print("Button Not Clickable or Overlay is in the way\n")
        try:
            publisher = get_publisher_text(edition_details_element_WebDriverWait_amount)
            clicked_button_test = "Pass"
        except:
            publisher=""
            clicked_button_test = "Fail"
    except:
        print("Unforeseen error: \n")
        publisher=""
        clicked_button_test = "Fail"

    # If the button is not found or not clickable, the get_publisher_text function will still run
    #print("Everything Failed: One last try: \n")
    #publisher = get_publisher_text()

    #============================================================================================================
    # D E F I N I T I O N    S E C T I O N
    #============================================================================================================
    try:
        page_count_element = driver.find_element(By.CSS_SELECTOR, 'p[data-testid="pagesFormat"]')
        page_count = page_count_element.text

    except NoSuchElementException:
        page_count = ""
    
    try:
        year_element = driver.find_element(By.CSS_SELECTOR, 'p[data-testid="publicationInfo"]')
        year = year_element.text
    except NoSuchElementException:
        year = ""
    
    try:
        review_count_element = driver.find_element(By.CSS_SELECTOR, 'span[data-testid="reviewsCount"]')
        review_count = review_count_element.text
        
        # converting string to interger with RegEx
        review_count_match = re.search(r'\d+', review_count)
        if review_count_match:
            review_count = int(review_count_match.group())
        else:
            review_count = 0
            
    except NoSuchElementException:
        review_count = 0

    try:
        rating_count_element = driver.find_element(By.CSS_SELECTOR, 'span[data-testid="ratingsCount"]')
        rating_count = rating_count_element.text

    except NoSuchElementException:
        rating_count = ""
    
    try:
        rating_element = driver.find_element(By.CLASS_NAME, 'RatingStatistics__rating')    
        rating = rating_element.text
        
    except NoSuchElementException:
        rating = ""
    
    try:
        genre_class_element = driver.find_element(By.CLASS_NAME, 'BookPageMetadataSection__genres')
        genres_text_element = genre_class_element.find_elements(By.CSS_SELECTOR, '.BookPageMetadataSection__genreButton .Button__labelItem')
        genre = genres_text_element[0].text
        
    except NoSuchElementException:
        genre = ""
    
    try:
        author_element = driver.find_element(By.CLASS_NAME, 'ContributorLink__name')
        author = author_element.text

    except NoSuchElementException:
        author = ""
    
    # assign the current datetime to this column for each row in the loop
    current_datetime = datetime.datetime.now()
    
    book_reviews = [title, page_count, year, review_count, rating, rating_count, genre, author, publisher, current_datetime]

    # current row in DataFrame. create these columns
    # and add book information to current dataframe row
    df.at[index, 'title'] = title
    df.at[index, 'page_count'] = page_count
    df.at[index, 'publisher'] = publisher
    df.at[index, 'year'] = year
    df.at[index, 'review_count'] = review_count
    df.at[index, 'rating'] = rating
    df.at[index, 'rating_count'] = rating_count
    df.at[index, 'genre'] = genre
    df.at[index, 'author'] = author
    df.at[index, 'scraped_at'] = current_datetime

    # ==================================================================
    # R E V I E W S
    # ==================================================================
    # iterating 5 times for reviews offset by 3 
    # list of elements "synopsis_and_review_list" has synopsis
    # and reviews
    
    # set this to the maximum number of reviews you want to capture
    max_reviews = 5  
    
    # index 0 has synopsis, index 1 & 2 are blank, 3-7 contain reviews
    review_index = 3 
    
    for i in range(max_reviews):
        if review_index < synopsis_length:
            # saving current review to temporary list
            book_reviews.append(synopsis_and_review_list[review_index].text)
            review_index += 1
        else:
            book_reviews.append("")
            break

    
    # ==================================================================
    # L O G
    # ==================================================================
    # T E S T   D E F I N I T I O N S
    # ------------------------------------------------------------------
    review_5_test = 'Pass' if synopsis_length >= 8 else 'Fail'
    publisher_test = 'Fail' if publisher == '' else 'Pass'
    print("===============================================================")
    print(f"            N E W   B O O K  S T A R T I N G:   #{index + 1}")
    print("===============================================================")
    print("                      L I N K")
    print("---------------------------------------------------------------")
    print(row['links'])
    print("---------------------------------------------------------------")
    print(f"{title}")
    print("---------------------------------------------------------------")
    print(f"5 Review Test: {review_5_test}")
    print("---------------------------------------------------------------")
    print(f"Clicked Button Test: {clicked_button_test}")
    print("---------------------------------------------------------------")
    print(f"Publisher Found Test: {publisher_test}")
    print("---------------------------------------------------------------")
    print(f"TIME STAMP: {current_datetime}")
    print("---------------------------------------------------------------")
    # ==================================================================
    # S A V I N G   P L A C E   A F T E R   E A C H   I T E R A T I O N
    # ==================================================================
    with open("reviews.csv", "a", newline = '', encoding = 'utf-8') as reviews_file:
        csv_writer = csv.writer(reviews_file)
        if not reviews_file_exists:
            csv_writer.writerow(['Book Name', 'page_count', 'year', 'review_count', 'rating', 'rating_count', 'genre', 'author', 'publisher', 'scraped_at', 'Review 1', 'Review 2', 'Review 3', 'Review 4', 'Review 5'])
            reviews_file_exists = True
        csv_writer.writerow(book_reviews)

    # ==================================================================
    # S A V I N G   P L A C E   A F T E R   E A C H   I T E R A T I O N
    # ==================================================================
    # save place of index to file for resuming later
    with open("index.txt", "w") as index_file:
        index_file.write(str(index + 1))

# D O N E    W I T H    S C R A P E R
driver.quit()

if not reviews_file_exists:
    open("reviews.csv", "a", newline = '', encoding = 'utf-8').close()

if not index_file_exists:
    open("index.txt", "a").close()

Output of last_index: 0
- Waiting 7 Seconds for Synopsis and Reviews to load....
Unforeseen error: 

            N E W   B O O K  S T A R T I N G:   #1
                      L I N K
---------------------------------------------------------------
https://www.goodreads.com/book/show/218495.Foley_is_Good?from_search=true&from_srp=true&qid=iVqnOFoTs7&rank=1
---------------------------------------------------------------
Foley is Good: And the Real World is Faker Than Wrestling
---------------------------------------------------------------
5 Review Test: Pass
---------------------------------------------------------------
Clicked Button Test: Fail
---------------------------------------------------------------
Publisher Found Test: Fail
---------------------------------------------------------------
TIME STAMP: 2023-03-23 10:24:37.305396
---------------------------------------------------------------
- Waiting 7 Seconds for Synopsis and Reviews to load....
Unforeseen error: 

            N

### The above code, for me, only pulls author and reviews. Needing to trouble-shoot

### This is the old, v7. Got 730 books by running overnight (below code). Use the above version.

In [28]:
# S C R A P I N G   B R O W S E R
driver = webdriver.Chrome()

reviews_file_exists = os.path.isfile("reviews.csv")
print("Does Review CSV File Exists?")
print(reviews_file_exists)
print("\n")

index_file_exists = os.path.isfile("index.txt")

# checking last value of index in order to continue from last position
if index_file_exists:
    with open("index.txt", "r") as index_file:
        last_index = int(index_file.read())
else:
    last_index = 0

print("Output of last_index")
print(last_index)

# iterate over the dataframe
for index, row in df.iloc[last_index:].iterrows():
    print("Ouput of index")
    print(index)
    
    print("Ouput of row")
    print(row)

    #============================================================================================================
    # L O A D    P A G E    O N    S C R A P I N G    B R O W S E R
    #============================================================================================================
    driver.get(row['links'])
    try:
        print("Waiting for Title Element to Load....")
        title_element = WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.CLASS_NAME, 'BookPageTitleSection__title')))
        print("Assigning Title")
        title = title_element.text
    except TimeoutException:
        print(f"Timed out while waiting for title for book {row['links']}, moving on to next book")
        continue
    
    print("Ouput of title")
    print(title)
    
    #============================================================================================================
    # P U B L I S H E R   D A T A
    #============================================================================================================
    # First, try to find and click the button
    button_found = False
    try:
        time.sleep(10)
        button = driver.find_element(By.XPATH, '//button[aria-label="Book details and editions"]')
        

        button.click()
        button_found = True
        # Wait for the publisher element to load
        WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.CLASS_NAME, "EditionDetails")))
    except (NoSuchElementException, ElementNotInteractableException, ElementClickInterceptedException):
        print("Button not found or not clickable")

    # If the button is not found or not clickable, the get_publisher_text function will still run
    publisher = get_publisher_text()

    # Print the extracted publisher text
    if publisher is not None:
        print("=====================")
        print(" P U B L I S H E R ")
        print("=====================")
        print(publisher)
        print("=====================")
    else:
        print("Publisher text not found")


    #============================================================================================================
    # D E F I N I T I O N    S E C T I O N
    #============================================================================================================
    try:
        print("Waiting for Synopsis and Reviews to load....")
        time.sleep(20)
        synopsis_and_review_list = WebDriverWait(driver, 20).until(EC.presence_of_all_elements_located((By.CLASS_NAME, 'Formatted')))
        print(f"The variable length of book {index+1} = ")
        print(len(synopsis_and_review_list))
        synopsis_length = len(synopsis_and_review_list)
        print("Output of synopsis_length")
        print(synopsis_length)
    except TimeoutException:
        print(f"Timed out while waiting for synopsis and review list for book {title}, moving on to next book")
        continue
    
    try:
        page_count_element = driver.find_element(By.XPATH, '//p[data-testid="pagesFormat"]')
        page_count = page_count_element.text  
        
        print("Ouput of page_count")
        print(page_count)
    except NoSuchElementException:
        page_count = ""
    
    try:
        year_element = driver.find_element(By.XPATH, '//p[data-testid="publicationInfo"]')
        year = year_element.text
        
        print("Ouput of year")
        print(year)
    except NoSuchElementException:
        year = ""
    
    try:
        review_count_element = driver.find_element(By.XPATH, '//span[data-testid="reviewsCount"]')
        review_count = review_count_element.text
        
        print("Ouput of review_count")
        print(review_count)
        
        # converting string to interger with RegEx
        review_count_match = re.search(r'\d+', review_count)
        if review_count_match:
            review_count = int(review_count_match.group())
            print("Ouput of RegEx: review_count")
            print(review_count)
        else:
            review_count = 0
            print("Ouput of No_RegEx: review_count")
            print(review_count)
            
    except NoSuchElementException:
        review_count = 0
        print("Ouput of No_Count: review_count")
        print(review_count)
    
    try:
        rating_count_element = driver.find_element(By.XPATH, '//span[data-testid="ratingsCount"]')
        rating_count = rating_count_element.text 
        print("Ouput of rating_count")
        print(rating_count)
    except NoSuchElementException:
        rating_count = ""
    
    try:
        rating_element = driver.find_element(By.XPATH, '//RatingStatistics__rating')
        rating = rating_element.text
        print("Ouput of rating")
        print(rating)
        
    except NoSuchElementException:
        rating = ""
    
    try:
        genre_class_element = driver.find_element(By.XPATH, '//BookPageMetadataSection__genres')
        genres_text_element = genre_class_element.find_elements(By.XPATH, '//.BookPageMetadataSection__genreButton .Button__labelItem')
        genre = genres_text_element[0].text
        print("Ouput of genre")
        print(genre)
        
    except NoSuchElementException:
        genre = ""
    
    try:
        author_element = driver.find_element(By.XPATH, '//ContributorLink__name')('ContributorLink__name')
        author = author_element.text
        print("Ouput of author")
        print(author)

    except NoSuchElementException:
        author = ""
        
    book_reviews = [title, page_count, year, review_count, rating, rating_count, genre, author,publisher]
    
    # current row in DataFrame. create these columns
    # and add book information to current dataframe row
    df.at[index, 'page_count'] = page_count
    df.at[index, 'publisher'] = publisher
    df.at[index, 'year'] = year
    df.at[index, 'review_count'] = review_count
    df.at[index, 'rating'] = rating
    df.at[index, 'rating_count'] = rating_count
    df.at[index, 'genre'] = genre
    df.at[index, 'author'] = author

    
    # =====================
    # T E S T   P R I N T
    # =====================
    print(f"Book {index}:")
    print(title)
    print("==============")
    print(page_count)
    print("\n")
    print("==============")
    print(year)
    print("\n")
    print("==============")
    print("Total Reviews: ")
    print(review_count)
    print("\n")
    print("==============")
    print(rating)
    print("\n")
    print("==============")
    print(rating_count)
    print("\n")
    print("==============")
    print(genre)
    print("\n")
    print("==============")
    print(author)
    print("\n")
    print("==============")
    print(publisher)
    print("\n")
    # ==================================================================
    # R E V I E W S
    # ==================================================================
    # iterating 5 times for reviews offset by 3 
    # list of elements "synopsis_and_review_list" has synopsis
    # and reviews
    review_index = 3
    for i in range(5):
        if review_index < synopsis_length:
            print(f"Review {i + 1}")
            print("==============")
            print(synopsis_and_review_list[review_index].text)

            # saving current review to temporary list
            book_reviews.append(synopsis_and_review_list[review_index].text)
            review_index += 1
        else:
            book_reviews.append("")
    # ==================================================================
    # S A V I N G   P L A C E   A F T E R   E A C H   I T E R A T I O N
    # ==================================================================
    with open("reviews.csv", "a", newline='', encoding='utf-8') as reviews_file:
        csv_writer = csv.writer(reviews_file)
        if not reviews_file_exists:
            csv_writer.writerow(['Book Name', 'page_count', 'year', 'review_count', 'rating', 'rating_count', 'genre', 'author', 'publisher', 'Review 1', 'Review 2', 'Review 3', 'Review 4', 'Review 5'])
            reviews_file_exists = True
        csv_writer.writerow(book_reviews)

    # ==================================================================
    # S A V I N G   P L A C E   A F T E R   E A C H   I T E R A T I O N
    # ==================================================================
    # save place of index to file for resuming later
    with open("index.txt", "w") as index_file:
        index_file.write(str(index + 1))

# D O N E    W I T H    S C R A P E R
driver.quit()

if not reviews_file_exists:
    open("reviews.csv", "a", newline='', encoding='utf-8').close()

if not index_file_exists:
    open("index.txt", "a").close()

Does Review CSV File Exists?
True


Output of last_index
70
Ouput of index
70
Ouput of row
links           https://www.goodreads.com/book/show/122902093-...
page_count                                                    NaN
publisher                                                     NaN
year                                                          NaN
review_count                                                  NaN
rating                                                        NaN
rating_count                                                  NaN
genre                                                         NaN
author                                                        NaN
Name: 70, dtype: object
Waiting for Title Element to Load....
Assigning Title
Ouput of title
The day of the jackal / by Frederick Forsyth
Button not found or not clickable
Timeout: EditionDetails element not found within the specified time
 P U B L I S H E R 

Waiting for Synopsis and Reviews to load....
The varia

Waiting for Title Element to Load....
Assigning Title
Ouput of title
The Word
Button not found or not clickable
Timeout: EditionDetails element not found within the specified time
 P U B L I S H E R 

Waiting for Synopsis and Reviews to load....
The variable length of book 73 = 
33
Output of synopsis_length
33
Ouput of No_Count: review_count
0
Book 72:
The Word






Total Reviews: 
0

















Review 1
THE WORD is similar to Dan Brown's THE DA VINCI CODE.

Irving Wallace provides a lot of interesting details about how the New Testament was written, how Bibles were published, and the historical facts surrounding the life of Christ.

This novel is very long, with too many unnecessary subplots and situations, but it is also thought-provoking.
Review 2
If this wasn't book 49 of my 50 book challenge I would have abandoned it 300 pages ago. I keep reading the little snippets of reviews on the first page that call this book "thrilling" and wondering what book the reviewer read. The ed

Waiting for Title Element to Load....
Assigning Title
Ouput of title
The Henry Family #1
The Winds of War
Button not found or not clickable
Timeout: EditionDetails element not found within the specified time
 P U B L I S H E R 

Waiting for Synopsis and Reviews to load....
The variable length of book 74 = 
33
Output of synopsis_length
33
Ouput of No_Count: review_count
0
Book 73:
The Henry Family #1
The Winds of War






Total Reviews: 
0

















Review 1
“They found the narrow tarred roads filling with people on foot and horse-drawn wagons laden with children, furniture, squawking geese, and the like. Some peasants drove along donkeys piled with household goods, or a few mooing cows. Marching soldiers now and then forced the car off the road. A troop of cavalry trotted by on gigantic dappled horses. The dusty riders chatted as they rode, strapping fellows with helmets and sabres glittering in the morning sun. They laughed, flashing white teeth, twirling their moustaches, gla

Review 4
Masterpiece. I truly felt a part of this book as if I were being swept into WW2 along with them all.

Possibly time for a reread or a good audio version. The film is excellent as well.
Review 5
The Winds of War (The Henry Family #1), Herman Wouk
The Winds of War is Herman Wouk's second book about World War II, the first being The Caine Mutiny (1951). Published in 1971, it was followed up seven years later by War and Remembrance. The novel features a mixture of real and fictional characters that are all connected to the extended family of Victor "Pug" Henry, a fictional middle-aged Naval Officer and confidant of President Franklin Delano Roosevelt. The story arc begins six months before Germany's invasion of Poland in September 1939 and ends shortly after the attack on Pearl Harbor on December 7, 1941, when the United States and, by extension, the Henry family, enters the war as well.
تاریخ نخستین خوانش: سال 1987 میلادی
عنوان: گردباد (رمان تاریخی) – دو جلدی. نویسنده: هرمان ووک؛

***5 STAR STORY ELEMENT ROLL CALL***

Nazis........"Here".......

International Intrigue........"Present".......

.........."Here"..........

.........."Here, Sir"..........

.........."Present"..........


.........Uh, Compelling Main Character......Anyone.......Main Character we care about......SHIT.....


.........hello....Excitement, Suspense.....Anyone.....has anyone seen any hint of excitement or suspense in this book......anywhere at all.....come on people......





On paper this book had 4 or 5 stars written all over it and I really thought I was going to love it. A well-written political thriller involving the hunting down of a Nazi war criminal and a worldwide secret organization of former SS members trying to reclaim power...what exactly is not to love?

Apparently, much, because in the end, it fell shorter than "Mini Me" which left me floating in disappointment.

The title of the book is derived from the German Acronyn O.D.E.S.S.A (Organisation der Ehemaligen SS-Angehörige

...

Assigning Title
Ouput of title
An Hour Before Daylight: Memories of a Rural Boyhood
Button not found or not clickable
Timeout: EditionDetails element not found within the specified time
 P U B L I S H E R 

Waiting for Synopsis and Reviews to load....
The variable length of book 726 = 
33
Output of synopsis_length
33
Ouput of No_Count: review_count
0
Book 725:
An Hour Before Daylight: Memories of a Rural Boyhood






Total Reviews: 
0

















Review 1
What a privilege to step inside the childhood of one of the most extraordinary living Americans. This is easily in the top 5 books I've read in 2011.

(by the way: I feel like this book never got the press it deserved because it came out late 2001... oops).

I wasn't expecting to read this in 48 hours... and yet, I couldn't put it down. This book, a collection of memories from Carter's upbringing in rural Georgia during the depression, paints such a vivid picture of that time and place in America that it's a valuable read for an

Waiting for Title Element to Load....
Assigning Title
Ouput of title
The O'Reilly Factor: The Good, the Bad, and the Completely Ridiculous in American Life
Button not found or not clickable
Timeout: EditionDetails element not found within the specified time
 P U B L I S H E R 

Waiting for Synopsis and Reviews to load....
The variable length of book 728 = 
33
Output of synopsis_length
33
Ouput of No_Count: review_count
0
Book 727:
The O'Reilly Factor: The Good, the Bad, and the Completely Ridiculous in American Life






Total Reviews: 
0

















Review 1
The entirety of the male species is sex starved! They are no more than a bunch of horny bastards, according to Bill O’Reilly’s Sex Factor. Men think of “NOTHING” but sex and rightly so because that’s just the way they are – sex starved monsters. “If we aren’t having sex on a daily basis, we are thinking about it all the time. I mean, all the time” (p.29)… “Women to men are just sex objects and no matter what a man says to yo

Waiting for Title Element to Load....
Assigning Title
Ouput of title
Study Guide: Seabiscuit by Laura Hillenbrand
Button not found or not clickable
Timeout: EditionDetails element not found within the specified time
 P U B L I S H E R 

Waiting for Synopsis and Reviews to load....
The variable length of book 729 = 
3
Output of synopsis_length
3
Ouput of No_Count: review_count
0
Book 728:
Study Guide: Seabiscuit by Laura Hillenbrand






Total Reviews: 
0

















Ouput of index
729
Ouput of row
links           https://www.goodreads.com/book/show/55358.Geor...
page_count                                                    NaN
publisher                                                     NaN
year                                                          NaN
review_count                                                  NaN
rating                                                        NaN
rating_count                                                  NaN
genre                        

Waiting for Title Element to Load....
Assigning Title
Ouput of title
Foley is Good: And the Real World is Faker Than Wrestling


KeyboardInterrupt: 